<a href="https://colab.research.google.com/github/LohitPotnuru/SplitOperator/blob/main/schrodinger_classical.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from matplotlib import animation, rc, pyplot as plt
from IPython.display import HTML
import numpy as np

In [3]:
'''constants'''
N=500 #grid points
hbar=1 #reduced plancks constant
dt=0.5 #delta t
m=1 #mass in au

'''spatial grid'''
xMin=0
xMax=500
x=np.linspace(xMin, xMax, N)

'''momentum grid'''
p=np.arange(-N/2, N/2)*((2*np.pi*hbar)/(N*((xMax-xMin)/(N-1))))

'''wavefunction: guassian wavepacket'''
k0=m/2 #initial momentum
x0=xMax/2 #initial position
sigma=(xMax-xMin)/30 #width
psi=(1/(sigma*np.sqrt(2*np.pi)))*np.exp(-.5*((x-x0)/sigma)**2)*np.exp(-1j*k0*x)

'''potential operator+propogator'''
Vhat=np.zeros_like(x) #nothing
Vhat[400:499]=1 #well between x=[400,499]
Vprop=np.exp(-1j*dt*Vhat/(2*hbar)) #half step

'''kinetic operator+propogator'''
That=p**2/(2*m)
Tprop=np.exp(-1j*dt*That/hbar)

'''function for one step of split operator method'''
def splitOperator(psi,Vprop=Vprop,Tprop=Tprop):
  psi*=Vprop #1/2 step of potential propagator
  psi_p=np.fft.fft(psi) #shift to momentum basis
  psi_p*=Tprop #kinetic propagator
  psi=np.fft.ifft(psi_p) #shift back to spatial basis
  psi*=Vprop #1/2 step of potential propagator
  return psi


In [4]:
'''animate'''
# First set up the figure, the axis, and the plot element we want to animate
fig, ax = plt.subplots()
plt.close()

### parameters for plot
ax.set_xlim(( 0, 500))
ax.set_ylim((-0.001, 0.001))

line, = ax.plot([], [], lw=2)
lineV, = ax.plot([], [], lw=2)

# initialization function: plot the background of each frame
def init():
    line.set_data([], [])
    lineV.set_data([], [])
    return (line, lineV,)

def animate(i):
  global psi
  psi=splitOperator(psi)
  line.set_data(x, np.conj(psi)*psi)
  lineV.set_data(x, Vhat)
  return(line, lineV,)

anim = animation.FuncAnimation(fig, animate, init_func=init,
                             frames=400, interval=10, blit=True)

# Note: below is the part which makes it work on Colab
rc('animation', html='jshtml')
anim

/usr/local/lib/python3.7/dist-packages/numpy/core/_asarray.py:83: ComplexWarning: Casting complex values to real discards the imaginary part
  return array(a, dtype, copy=False, order=order)
